In [1]:
import numpy as np
import optuna
from optuna.visualization import plot_param_importances, plot_contour
import matplotlib.pyplot as plt

# Załóżmy, że masz już zaimportowane klasy:
# from your_module import TSPProblem, DualPheromoneACO, PheromoneConfig, ExplorationConfig, ExplorationDecayType
from tsp_problem import TSPProblem
from dual_pheromone_tsp import DualPheromoneACO, PheromoneConfig, ExplorationConfig, ExplorationDecayType

def objective(trial):
    """Funkcja celu dla optymalizacji Optuna"""

    # Stały seed dla reproducibility
    np.random.seed(42)
    coords = np.random.rand(100, 2)

    # Sugerowane parametry przez Optuna
    n_ants = trial.suggest_int('n_ants', 25, 250)
    n_iterations = int(8000 / n_ants)  # Zależność od n_ants

    pheromone_reward_factor = trial.suggest_float('pheromone_reward_factor', 1, 1000)
    negative_pheromone_scaling = trial.suggest_float('negative_pheromone_scaling', 0.001, 0.7)

    initial_rate = trial.suggest_float('initial_rate', 0.1, 0.4)

    alpha = trial.suggest_float('alpha', 0.1, 3.0)
    beta = trial.suggest_float('beta', 2.0, 5.0)
    gamma = trial.suggest_float('gamma', 0.1, 5.0)

    rho_pos = trial.suggest_float('rho_pos', 0.01, 0.5)
    rho_neg = trial.suggest_float('rho_neg', 0.01, 0.5)

    # n_reinforce musi być mniejsze niż n_ants/2
    max_reinforce = min(50, int(n_ants // 2))
    if max_reinforce < 2:
        max_reinforce = 2
    n_reinforce = trial.suggest_int('n_reinforce', 2, max_reinforce)

    elite_boost = trial.suggest_categorical('elite_boost', [True, False])

    try:
        # Tworzenie problemu TSP
        problem = TSPProblem(coords)

        # Konfiguracja feromonów
        pheromone_config = PheromoneConfig(
            min_pheromone=1e-6,  # Stała wartość
            pheromone_reward_factor=pheromone_reward_factor,
            negative_pheromone_scaling=negative_pheromone_scaling
        )

        # Konfiguracja eksploracji
        exploration_config = ExplorationConfig(
            initial_rate=initial_rate,
            final_rate=0.0,  # Stała wartość
            decay_type=ExplorationDecayType.LINEAR  # Stała wartość
        )

        # Tworzenie algorytmu ACO
        dual_aco = DualPheromoneACO(
            problem=problem,
            n_ants=n_ants,
            n_iterations=n_iterations,
            alpha=alpha,
            beta=beta,
            gamma=gamma,
            rho_pos=rho_pos,
            rho_neg=rho_neg,
            n_reinforce=n_reinforce,
            elite_boost=elite_boost,
            pheromone_config=pheromone_config,
            exploration_config=exploration_config,
        )

        # Inicjalizacja i uruchomienie
        dual_aco.init_progress()

        while not dual_aco.stopping_condition_is_met():
            dual_aco.step()
            dual_aco.update_progress()

        # Zwracamy długość najlepszej trasy (minimalizujemy)
        best_result = dual_aco.result()
        return best_result.objectives[0]

    except Exception as e:
        print(f"Error in trial: {e}")
        # Zwracamy wysoką wartość w przypadku błędu
        return float('inf')

def run_optimization():
    """Uruchamia optymalizację hiperparametrów"""

    # Tworzenie studium Optuna
    study = optuna.create_study(
        direction='minimize',  # Minimalizujemy długość trasy
        study_name='TSP_Hyperparameter_Optimization'
    )

    print("Rozpoczynam optymalizację hiperparametrów...")
    print("Liczba prób: 100")
    print("Problem: TSP z 50 punktami")

    # Uruchomienie optymalizacji
    study.optimize(objective, n_trials=100, show_progress_bar=True)

    # Wyświetlenie wyników
    print("\n" + "="*50)
    print("WYNIKI OPTYMALIZACJI")
    print("="*50)

    print(f"Najlepsza wartość: {study.best_value:.6f}")
    print(f"Najlepsze parametry:")
    for param, value in study.best_params.items():
        print(f"  {param}: {value}")

    # Statystyki prób
    print(f"\nLiczba zakończonych prób: {len(study.trials)}")
    print(f"Liczba prób z błędami: {len([t for t in study.trials if t.state == optuna.trial.TrialState.FAIL])}")

    return study

def create_visualizations(study):
    """Tworzy wykresy analizy parametrów"""

    print("\nTworzenie wykresów...")

    # Wykres ważności parametrów
    fig1 = plot_param_importances(study)
    fig1.update_layout(
        title="Ważność hiperparametrów",
        title_x=0.5,
        width=1800,
        height=1600
    )
    fig1.show()

    # Wykres konturowy dla najważniejszych parametrów
    # Automatycznie wybierze 2 najważniejsze parametry
    try:
        fig2 = plot_contour(study)
        fig2.update_layout(
            title="Wykres konturowy najważniejszych parametrów",
            title_x=0.5,
            width=1800,
            height=1600
        )
        fig2.show()
    except ValueError as e:
        print(f"Nie można utworzyć wykresu konturowego: {e}")
        print("Spróbuj określić konkretne parametry dla wykresu konturowego.")

    # Możesz też utworzyć konkretny wykres konturowy dla wybranych parametrów:
    # fig3 = plot_contour(study, params=['alpha', 'beta'])
    # fig3.show()

def analyze_results(study):
    """Dodatkowa analiza wyników"""

    print("\n" + "="*50)
    print("DODATKOWA ANALIZA")
    print("="*50)

    # Top 10 najlepszych prób
    trials_df = study.trials_dataframe()
    top_trials = trials_df.nsmallest(10, 'value')

    print("Top 10 najlepszych wyników:")
    print(top_trials[['number', 'value']].to_string(index=False))

    # Korelacje parametrów z wynikami
    print(f"\nKorelacje parametrów z wartością celu:")
    correlations = trials_df.corr()['value'].sort_values(key=abs, ascending=False)
    for param, corr in correlations.items():
        if param != 'value' and not param.startswith('datetime') and not param.startswith('duration'):
            print(f"  {param}: {corr:.4f}")


In [2]:
study = run_optimization()
create_visualizations(study)
analyze_results(study)

print(f"\nAnaliza zakończona! Najlepszy wynik: {study.best_value:.6f}")

[I 2025-06-13 07:44:02,910] A new study created in memory with name: TSP_Hyperparameter_Optimization


Rozpoczynam optymalizację hiperparametrów...
Liczba prób: 100
Problem: TSP z 50 punktami


  0%|          | 0/100 [00:00<?, ?it/s]

[I 2025-06-13 07:44:38,255] Trial 0 finished with value: 8.036751387698848 and parameters: {'n_ants': 164, 'pheromone_reward_factor': 954.9750299101664, 'negative_pheromone_scaling': 0.36156797090770143, 'initial_rate': 0.1867820548917266, 'alpha': 1.7523399556671397, 'beta': 2.687965333673554, 'gamma': 4.769498062962849, 'rho_pos': 0.09736397538890275, 'rho_neg': 0.3468855873830102, 'n_reinforce': 27, 'elite_boost': True}. Best is trial 0 with value: 8.036751387698848.
[I 2025-06-13 07:45:12,921] Trial 1 finished with value: 7.983837729565507 and parameters: {'n_ants': 167, 'pheromone_reward_factor': 359.42695327754365, 'negative_pheromone_scaling': 0.2227372277142698, 'initial_rate': 0.30226455616904135, 'alpha': 1.7309796877546233, 'beta': 3.189713439810525, 'gamma': 1.6806981150730484, 'rho_pos': 0.23419552753229897, 'rho_neg': 0.25085444429663245, 'n_reinforce': 30, 'elite_boost': False}. Best is trial 1 with value: 7.983837729565507.
[I 2025-06-13 07:45:48,281] Trial 2 finished w

D:\Studia\semestr8\ioio\antmaxxing\discrete\dual_pheromone_tsp.py:238: RuntimeWarning: invalid value encountered in divide
  probabilities /= probabilities.sum()


...

[W 2025-06-13 08:42:39,891] Trial 5 is omitted in visualization because its objective value is inf or nan.
[W 2025-06-13 08:42:39,892] Trial 68 is omitted in visualization because its objective value is inf or nan.


[I 2025-06-13 08:42:39,863] Trial 99 finished with value: 8.16345025643471 and parameters: {'n_ants': 99, 'pheromone_reward_factor': 240.7637703406907, 'negative_pheromone_scaling': 0.642474917074122, 'initial_rate': 0.18704622234946267, 'alpha': 0.762301571670704, 'beta': 2.5732398606793287, 'gamma': 2.8816317714241135, 'rho_pos': 0.2648491950776828, 'rho_neg': 0.14516367176898476, 'n_reinforce': 15, 'elite_boost': False}. Best is trial 77 with value: 7.541903964219619.

WYNIKI OPTYMALIZACJI
Najlepsza wartość: 7.541904
Najlepsze parametry:
  n_ants: 53
  pheromone_reward_factor: 167.10254925648738
  negative_pheromone_scaling: 0.5933840860600831
  initial_rate: 0.2788416239995373
  alpha: 1.1359864952538263
  beta: 2.2631915690491096
  gamma: 3.134285302270179
  rho_pos: 0.22098693944129486
  rho_neg: 0.049740141236645316
  n_reinforce: 15
  elite_boost: False

Liczba zakończonych prób: 100
Liczba prób z błędami: 0

Tworzenie wykresów...


[W 2025-06-13 08:42:41,134] Trial 5 is omitted in visualization because its objective value is inf or nan.
[W 2025-06-13 08:42:41,135] Trial 68 is omitted in visualization because its objective value is inf or nan.



DODATKOWA ANALIZA
Top 10 najlepszych wyników:
 number    value
     77 7.541904
     83 7.562521
     54 7.577145
     91 7.608561
     63 7.614509
     57 7.615633
     70 7.626041
     75 7.635220
     62 7.637000
     15 7.661660

Korelacje parametrów z wartością celu:


ValueError: could not convert string to float: 'COMPLETE'